# Working with Apache Hudi tables
Use SQL on Athena Spark to create, analyze and manage Apache Hudi tables.

## Create database and Hudi table
First, we will create a database called hudidb that will be stored in the Glue Data Catalog followed by Hudi table creation.

In [ ]:
%%sql
CREATE DATABASE hudidb

We will create a hudi table pointing to a location in S3 where we will load the data. . Please note the table is of copy-on-write type. We have defined **station** and **date** as the multiple primary keys and preCombinedField as **year**. Also, the table is partitioned on **year**.

**Note**: Replace the location 's3://\<your-S3-bucket\>/\<prefix\>/' to your S3 bucket and prefix:

In [ ]:
%%sql
CREATE TABLE hudidb.noaa_hudi(
  station string, 
  date string, 
  latitude string, 
  longitude string, 
  elevation string, 
  name string, 
  temp string, 
  temp_attributes string, 
  dewp string, 
  dewp_attributes string, 
  slp string, 
  slp_attributes string, 
  stp string, 
  stp_attributes string, 
  visib string, 
  visib_attributes string, 
  wdsp string, 
  wdsp_attributes string, 
  mxspd string, 
  gust string, 
  max string, 
  max_attributes string, 
  min string, 
  min_attributes string, 
  prcp string, 
  prcp_attributes string, 
  sndp string, 
  frshtt string,
  year string)
USING HUDI
PARTITIONED BY (year)
TBLPROPERTIES(
    primaryKey = 'station,date',
    preCombineField = 'year',
    type = 'cow'
)
LOCATION 's3://<your-S3-bucket>/<prefix>/noaahudi/'

## Insert data into table

We will use INSERT INTO statement to populate above table by reading data from sparkblogdb.noaa_pq table created in the previous blog post.


In [ ]:
%%sql
INSERT INTO hudidb.noaa_hudi select * from sparkblogdb.noaa_pq

## Querying the Hudi table
Now that the table is created, let’s run a query to find the maximum recorded temperature for the 'SEATTLE TACOMA AIRPORT, WA US' location

In [ ]:
%%sql
select name, year, max(MAX) as maximum_temperature 
from hudidb.noaa_hudi
where name = 'SEATTLE TACOMA AIRPORT, WA US' 
group by 1,2

## Updating data in Hudi table

Let’s change the station name 'SEATTLE TACOMA AIRPORT, WA US' to 'Sea–Tac'. We can run UPDATE statement on Athena Spark to update the records of noaa_hudi table.

In [ ]:
%%sql
UPDATE hudidb.noaa_hudi 
SET name = 'Sea-Tac'
WHERE name = 'SEATTLE TACOMA AIRPORT, WA US'

We will run previous SELECT query to find the maximum recorded temperature for the 'Sea-Tac' location:

In [ ]:
%%sql
select name, year, max(MAX) as maximum_temperature 
from hudidb.noaa_hudi
where name = 'Sea-Tac' 
group by 1,2

## Time Travel

We can use time travel queries in SQL on Athena Spark to analyze past data snapshots. For example:

In [ ]:
%%sql
select name, year, max(MAX) as maximum_temperature 
from hudidb.noaa_hudi timestamp as of '20231201235343335'
where name = 'SEATTLE TACOMA AIRPORT, WA US' 
group by 1,2

This query checks the Seattle Airport temperature data as of a specific time in the past. The timestamp clause lets us travel back without altering current data.

## Optimize query speed with Clustering

To improve query performance, you can perform clustering on Hudi tables using SQL in Athena Spark.

In [ ]:
%%sql
CALL run_clustering(table => 'hudidb.noaa_hudi', order => 'name')

## Drop table and database
Run following Spark SQL to remove the hudi table created above and associated data from the S3 location.

In [ ]:
%%sql
DROP TABLE hudidb.noaa_hudi PURGE

Run following Spark SQL to remove the database hudidb

In [ ]:
%%sql
DROP DATABASE hudidb

Dropping the table and database deletes the metadata for these objects, but does not automatically delete the data files in Amazon S3. The files can be manually deleted if no longer needed.

To learn what all operations can be performed on Hudi tables using Athena Spark, please refer [SQL DDL](https://hudi.apache.org/docs/0.13.0/table_management) and [Procedures](https://hudi.apache.org/docs/0.13.0/procedures) section of [Hudi documentation](https://hudi.apache.org/docs/0.13.0/overview).